In [1]:
#Importing libraries
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.base import TransformerMixin
import numpy as np
import pandas as pd
from matplotlib import pyplot as plt
import nltk
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
import re
import requests
import seaborn as sns
import pprint, time
from sklearn.model_selection import train_test_split
nltk.download('treebank')
from nltk.tokenize import sent_tokenize
import string
from nltk.tokenize import RegexpTokenizer
from nltk.stem import WordNetLemmatizer
from nltk.stem.porter import PorterStemmer
from collections import Counter
from spellchecker import SpellChecker
import random
from sklearn_crfsuite import CRF
from sklearn_crfsuite import metrics
from sklearn_crfsuite import scorers
import base64
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.pipeline import Pipeline
from sklearn.metrics import accuracy_score, classification_report, confusion_matrix

nltk.download('punkt')

nltk.download('universal_tagset')

%matplotlib inline

punct = string.punctuation

[nltk_data] Downloading package treebank to
[nltk_data]     C:\Users\halapets\AppData\Roaming\nltk_data...
[nltk_data]   Package treebank is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\halapets\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package universal_tagset to
[nltk_data]     C:\Users\halapets\AppData\Roaming\nltk_data...
[nltk_data]   Package universal_tagset is already up-to-date!


In [2]:
#loading spacy
import spacy
nlp = spacy.load("en_core_web_lg")
nlp.max_length = 16000000

In [3]:
from spacy.lang.en.stop_words import STOP_WORDS
stopwords = list(STOP_WORDS)
stopwords

['us',
 'always',
 'except',
 'can',
 'per',
 'ours',
 'onto',
 'there',
 '‘s',
 'last',
 'yourself',
 'twelve',
 'really',
 'toward',
 'another',
 'whither',
 'my',
 'some',
 'same',
 'mine',
 'every',
 'full',
 'also',
 'which',
 'go',
 'up',
 'neither',
 'somewhere',
 'himself',
 'me',
 'no',
 'seemed',
 'six',
 'whom',
 'therefore',
 'n’t',
 'about',
 'should',
 "'ll",
 'only',
 'would',
 'four',
 'say',
 'namely',
 'yet',
 'wherever',
 'where',
 'keep',
 'at',
 'not',
 'of',
 'various',
 'whereas',
 'besides',
 'both',
 'whether',
 'may',
 'own',
 'almost',
 'hence',
 'how',
 'latter',
 'than',
 'after',
 'meanwhile',
 'amount',
 'the',
 'five',
 'might',
 'becomes',
 'few',
 'themselves',
 'we',
 'now',
 'take',
 'once',
 'call',
 'thereupon',
 "'ve",
 'hereafter',
 '’ll',
 'though',
 'are',
 'is',
 'why',
 'nevertheless',
 'fifty',
 'she',
 'on',
 'thereafter',
 "'s",
 'other',
 'within',
 'because',
 'someone',
 'but',
 'fifteen',
 'unless',
 'been',
 'put',
 'get',
 'thence',


In [4]:
LatestMobileReviews1 = pd.read_csv('C:\\Users\\halapets\\Documents\\LJMU Research_Sentiment Analysis\\LatestMobileReviews.csv',encoding='latin1')
LatestMobileReviews1.head()

Product                                      ReviewUpdated  \
0  Xiaomi Redmi Note 3  ['yet', 'another', 'value', 'money', 'product'...   
1  Xiaomi Redmi Note 3  ['awesome', 'marvelous', 'mobile', 'go', 'valu...   
2  Xiaomi Redmi Note 3  ['power', 'pack', 'review', 'redmi', 'note', '...   
3  Xiaomi Redmi Note 3  ['flagship', 'smartfone', 'phone', 'looks', 'v...   
4  Xiaomi Redmi Note 3  ['boon', 'mobile', 'master', 'piece', 'economi...   

   Rating                   Date    Website  \
0     3.0  Jul 17, 2016 10:59 PM  MouthShut   
1     5.0  Jul 17, 2016 10:42 PM  MouthShut   
2     5.0  Jul 17, 2016 06:18 PM  MouthShut   
3     4.0  Jul 17, 2016 04:44 PM  MouthShut   
4     5.0  Jul 17, 2016 12:32 PM  MouthShut   

                                        TitleGoodBad ProductPrice  \
0  Yet another Value for Money product from Xiaomi           9999   
1                                          Awesome           9999   
2                Power pack review on Redmi Note 3           9999   
3                 Flagship smartfone under 13000rs           9999   
4                                  Boon for mobile           9999   

  ProductPriceRange    Year  positive_negative  ...  Positive_Negative_Tag  \
0      Budget Range  2016.0                  1  ...        Positive Rating   
1      Budget Range  2016.0                  1  ...        Positive Rating   
2      Budget Range  2016.0                  1  ...        Positive Rating   
3      Budget Range  2016.0                  1  ...        Positive Rating   
4      Budget Range  2016.0                  1  ...        Positive Rating   

   LengthofReviews SentimentPolarity SentimentSubjectivity  \
0              344         -0.028571              0.576190   
1              276          0.780000              0.640000   
2              322          0.474444              0.477037   
3              333          0.502500              0.832500   
4              316          0.448571              0.627857   

   SentimentPolarityClass  AvgSentPolarity  AvgSentimentPolarityClass  \
0         Negative Rating         0.403533            Positive Rating   
1         Positive Rating         0.403533            Positive Rating   
2         Positive Rating         0.403533            Positive Rating   
3         Positive Rating         0.403533            Positive Rating   
4         Positive Rating         0.403533            Positive Rating   

  AvgSentimentSubjectivity                                     ReviewUpdated1  \
0                      NaN  Yet another Value for Money product from Xiaom...   
1                      NaN  Awesome  Marvelous Mobile just go for it., Val...   
2                      NaN  Power pack review on Redmi Note 3  REDMI NOTE ...   
3                      NaN  Flagship smartfone under 13000rs  This phone l...   
4                      NaN  Boon for mobile  Master piece in such a econom...   

                                      ReviewUpdated2  
0  Yet another Value for Money product from Xiaom...  
1  Awesome  Marvelous Mobile just go for it., Val...  
2  Power pack review on Redmi Note 3  REDMI NOTE ...  
3  Flagship smartfone under 13000rs  This phone l...  
4  Boon for mobile  Master piece in such a econom...  

[5 rows x 23 columns]

In [5]:
LatestMobileReviews1.shape

(160057, 23)

In [6]:
#tokenization and text preprocessing
def text_data_cleaning(sentence):
    doc = nlp(sentence)
    
    tokens = []
    for token in doc:
        if token.lemma_ != "-PRON-" or token.pos_ != "AUX" or token.pos_ != "NUM" or token.pos_ != "SYM" or token.pos_ != "ADP"  :
            temp = token.lemma_.lower().strip()
        tokens.append(temp)
        
    
    cleaned_tokens = []
    for token in tokens:
        if token not in stopwords and token not in punct and token.isalpha():
            cleaned_tokens.append(token)
    return cleaned_tokens

In [7]:
text_data_cleaning("    Hello how are you. Like this video! Please advise $")

['hello', 'like', 'video', 'advise']

In [8]:
#word vectorization using tfidf
tfidf = TfidfVectorizer(tokenizer = text_data_cleaning)

In [9]:
LatestMobileReviews1 = LatestMobileReviews1
# identifying products by count of reviews
LatestMobileReviews1Counts=pd.DataFrame(LatestMobileReviews1.groupby("Product").agg({"Product":"count"}))
LatestMobileReviews1Counts.head()
LatestMobileReviews1Counts.rename(columns = {"Product":"CountofReviews"},inplace = True)
LatestMobileReviews1Counts.sort_values("CountofReviews", ascending = False, inplace = True)
LatestMobileReviews1Counts =LatestMobileReviews1Counts.head(20)
LatestMobileReviews1Counts.to_csv("LatestTopProducts by ReviewCounts.csv", header = True)

LatestMobileReviews1Counts.head(20)

CountofReviews
Product                                         
Xiaomi Redmi Note 3                        12762
Samsung Galaxy J2 6 2016 Edition            8543
Xiaomi Redmi Note 4 4GB RAM                 7815
Xiaomi Redmi 3S Prime                       6855
Xiaomi Redmi 4A                             5721
Xiaomi Mi A1                                5140
Samsung Galaxy J7 Prime                     4907
Samsung Galaxy J7 6 2016 Edition            3326
Samsung Galaxy J7                           3309
Motorola Moto G4 Plus                       3024
Apple iPhone 5S                             2974
Reliance JioPhone                           2955
Vivo V5                                     2645
Samsung Galaxy J7 Pro                       2310
Lenovo Vibe K4 Note                         2168
Samsung Galaxy J2                           2110
Lenovo K3 Note                              2021
Samsung Galaxy J7 Max                       1836
Apple iPhone 6S                             1811
Samsung Galaxy Note 3                       1789

In [10]:
#filtering the LatestMobileReviews1 dataset for Products having at least 1000 reviews
#LatestMobileReviews1= pd.merge(LatestMobileReviews1,LatestMobileReviews1Counts, how = "inner", left_on = "Product", right_index = True)
#LatestMobileReviews1.shape #265808,11a
#LatestMobileReviews1.head()

In [11]:
#Filtering the data with Products more than 1000 reviews and Year 2016 onwards
#LatestMobileReviews1 = LatestMobileReviews1[(LatestMobileReviews1["CountofReviews_y"] >= 1000)]
#LatestMobileReviews1.shape

In [12]:
X = LatestMobileReviews1[['Product','ReviewUpdated1']]
y= LatestMobileReviews1 ['positive_negative']
len(X)
len(y)

160057

In [13]:
X_transformed = tfidf.fit_transform(X['ReviewUpdated1'])

In [14]:
X_transformed.shape

(160057, 101644)

In [15]:
y.shape



(160057,)

In [16]:
#Converting TFIDF Matrix to dataframe
#df_TFIDF = pd.DataFrame(X_transformed.toarray(), columns=tfidf.get_feature_names())

In [17]:
#df_TFIDF.shape

In [18]:
len(X['Product'])

160057

### Features Extraction using Gini Index, Information Gain and Chi Square 

#### Features Selection using statistical method Chi Square

In [19]:
### Features selection using Chi Squared statistical test
from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import chi2

#features selection using chi square
test = SelectKBest(score_func=chi2, k=300)

#Fit the function for ranking the features by score
fit_X2 = test.fit(X_transformed, y)
               
#Apply the transformation on to dataset
features = fit_X2.transform(X_transformed)





In [20]:
#Summarize selected features 
print(features)

  (0, 50)	0.164311386371995
  (0, 91)	0.23138623045634582
  (0, 232)	0.13763050779428265
  (0, 245)	0.137914081907981
  (0, 297)	0.09723748925138466
  (0, 170)	0.11310415215417007
  (1, 112)	0.10393742902317313
  (1, 97)	0.1711112999167153
  (1, 108)	0.13125100242492352
  (1, 154)	0.10106269418657772
  (1, 13)	0.12101446533726243
  (1, 170)	0.1424035523527881
  (2, 208)	0.09723088329549605
  (2, 137)	0.2766605974087662
  (2, 110)	0.3736079234264746
  (2, 176)	0.24003464922606843
  (2, 214)	0.22933352643070407
  (2, 188)	0.21782619361821937
  (2, 197)	0.1621569785165275
  (2, 112)	0.2217038653083013
  (2, 154)	0.10778595425253205
  (2, 297)	0.2611423488466781
  (3, 243)	0.11889581831537661
  (3, 45)	0.11517368945362982
  (3, 69)	0.08502097828356206
  :	:
  (160055, 9)	0.12867619259603144
  (160055, 262)	0.10784872515530684
  (160055, 253)	0.12933937858857314
  (160055, 85)	0.23236066909208777
  (160055, 76)	0.12683030972534548
  (160055, 28)	0.10200694870728799
  (160055, 230)	0.1251727

In [21]:


mask = test.get_support() #list of booleans
new_features = [] # The list of your K best features

for bool, feature in zip(mask, tfidf.get_feature_names()):
    if bool:
        new_features.append(feature)
        


In [22]:
len(new_features)

300

In [23]:
features_df = pd.DataFrame(features.todense(), columns=new_features)

In [24]:
features_df.head()

able  advertise  advertisement  affordable  ago  alot  amazing  android  \
0   0.0        0.0            0.0         0.0  0.0   0.0      0.0      0.0   
1   0.0        0.0            0.0         0.0  0.0   0.0      0.0      0.0   
2   0.0        0.0            0.0         0.0  0.0   0.0      0.0      0.0   
3   0.0        0.0            0.0         0.0  0.0   0.0      0.0      0.0   
4   0.0        0.0            0.0         0.0  0.0   0.0      0.0      0.0   

   angry  app  ...  world  worst  worth  worthless  wrong  wrost    x  \
0    0.0  0.0  ...    0.0    0.0    0.0        0.0    0.0    0.0  0.0   
1    0.0  0.0  ...    0.0    0.0    0.0        0.0    0.0    0.0  0.0   
2    0.0  0.0  ...    0.0    0.0    0.0        0.0    0.0    0.0  0.0   
3    0.0  0.0  ...    0.0    0.0    0.0        0.0    0.0    0.0  0.0   
4    0.0  0.0  ...    0.0    0.0    0.0        0.0    0.0    0.0  0.0   

     xiaomi   yu  yureka  
0  0.097237  0.0     0.0  
1  0.000000  0.0     0.0  
2  0.261142  0.0     0.0  
3  0.092806  0.0     0.0  
4  0.000000  0.0     0.0  

[5 rows x 300 columns]

In [25]:
features_df.to_csv("features_df_Chi_Square.csv",header = True, index = False)

In [26]:
features_df.columns

Index(['able', 'advertise', 'advertisement', 'affordable', 'ago', 'alot',
       'amazing', 'android', 'angry', 'app',
       ...
       'world', 'worst', 'worth', 'worthless', 'wrong', 'wrost', 'x', 'xiaomi',
       'yu', 'yureka'],
      dtype='object', length=300)

### Recursive Feature Elimination

In [27]:
#Import sklearn's feature selection algorithm 
#from sklearn.feature_selection import RFE

In [28]:
#Import LogisticRegression for performing chi square test 
#from sklearn.linear_model import LogisticRegression

In [29]:
#Feature extraction
#model = LogisticRegression() 
#rfe = RFE(model, 300)

In [30]:
#fit = rfe.fit(X_transformed, y)

In [31]:
#print("Num Features: %d"% fit.n_features_) 

In [32]:
#print("Selected Features: %s"% fit.support_) *

In [33]:
#print("Feature Ranking: %s"% fit.ranking_)

In [34]:
#Apply the transformation on to dataset
#features = fit.transform(X_transformed)

### Choosing Important features using Features Importance (Gini Index)

In [35]:
#Random Forests allow us to look at feature importances, which is the how much the Gini Index 
#for a feature decreases at each split. The more the Gini Index decreases for a feature, 
#the more important it is. The figure below rates the features from 0–100, with 100 being the most important.
#Import Random Forest classifier class from sklearn
from sklearn.ensemble import RandomForestClassifier
from sklearn.tree import DecisionTreeClassifier

In [36]:
#Import feature selector
from sklearn.feature_selection import SelectFromModel


In [37]:
#Train, Test split
#X_train, X_test, y_train, y_test = train_test_split(X_transformed, y, test_size = 0.3, random_state = 1001)


In [38]:
#Extract attribute names from the data frame

feat_labels=tfidf.get_feature_names()
feat_labels

['aa',
 'aaa',
 'aaaa',
 'aaaaaaa',
 'aaaaaaaaaaa',
 'aaaaaaaaaaaaaaaa',
 'aaaaaaaaaaaaaaaaaaaaaaaaaaaaa',
 'aaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaa',
 'aaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaa',
 'aaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaa',
 'aaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaa',
 'aaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaashdhdhdbdbdbdhdxbhdhxbhdhdhebdhdhdbdbdbdbbdbdhdhdbdbc',
 'aaaaaaaaaaaaaaaaaaawwwwwwwwwwwooooooooooooooooooossssssssssssssssssssssooooooooooooooooommmmmmmmmmmmmmmmmmmmmmeeeeeeeeeeeeeeee',
 'aaaaaaaaaaaaaaamazing',
 'aaaaaaaaaaaaaaawwwwwwweeeeeeeeeeeeeeeeeeesssssssssssssssssssssssssssssss',
 'aaaaaaaaaa

In [39]:
#Create a random forest classifier with the following Parameters
trees = 100
#max_feat= 8
#max_depth = 30

In [40]:
clf_Gini = RandomForestClassifier(n_estimators=100,

#max_features=max_feat,

#max_depth=max_depth,

random_state=0,)


In [41]:
#Train the classifier 
clf_Gini.fit(X_transformed, y)

RandomForestClassifier(bootstrap=True, ccp_alpha=0.0, class_weight=None,
                       criterion='gini', max_depth=None, max_features='auto',
                       max_leaf_nodes=None, max_samples=None,
                       min_impurity_decrease=0.0, min_impurity_split=None,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, n_estimators=100,
                       n_jobs=None, oob_score=False, random_state=0, verbose=0,
                       warm_start=False)

In [42]:
pre_Gini = clf_Gini.predict(X_transformed)
len(pre_Gini)


160057

In [43]:
#Function to evaluate model performance

def getAccuracy(pre,ytest): 
    count = 0
    for i in range(len(ytest)):
        if ytest[i]==pre[i]: 
            count+=1
            acc = float(count)/len(ytest)
            return acc

In [44]:
#Evaluate the model performance for the test data
target_names = ['class 0', 'class 1']
ClassificationReport_Gini=classification_report(y, pre_Gini, target_names=target_names)
ClassificationReport_Gini

#'              precision    recall  f1-score   support\n\n     
#class 0       1.00      1.00      1.00     25866\n     
#class 1       1.00      1.00      1.00    134191\n\n    
#accuracy                          1.00    160057\n   
#macro avg     1.00      1.00      1.00    160057\n
#weighted avg  1.00      1.00      1.00    160057\n'

'              precision    recall  f1-score   support\n\n     class 0       1.00      1.00      1.00     25866\n     class 1       1.00      1.00      1.00    134191\n\n    accuracy                           1.00    160057\n   macro avg       1.00      1.00      1.00    160057\nweighted avg       1.00      1.00      1.00    160057\n'

In [45]:
accuracy_score(y, pre_Gini) #0.9999937522257696

0.9999937522257696

In [46]:
for feature in zip(feat_labels, clf_Gini.feature_importances_):
    print(feature)

('aa', 3.3147774309449525e-05)
('aaa', 3.880986601602953e-06)
('aaaa', 1.8180618968884686e-06)
('aaaaaaa', 1.1587854262720944e-08)
('aaaaaaaaaaa', 7.026575904621997e-08)
('aaaaaaaaaaaaaaaa', 3.1686062801608706e-07)
('aaaaaaaaaaaaaaaaaaaaaaaaaaaaa', 2.633606741914659e-09)
('aaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaa', 5.906376081609527e-10)
('aaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaa', 9.241091147604766e-11)
('aaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaa', 7.631571284723599e-10)
('aaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaa', 1.0308545792520181e-07)
('aaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaashdhdhdbdbdbdhdxbhdhxbhdhdhebdhdhdbdbdbdbbdb

('affter', 6.329396098370752e-06)
('affurd', 4.92887795422335e-06)
('afgord', 1.0313998404877078e-09)
('afgordable', 2.3552064285604073e-07)
('aficionado', 6.026744622426084e-06)
('afiger', 2.0188839664015638e-08)
('afinger', 0.0)
('afingerprint', 2.748819353319389e-09)
('afirst', 6.874717967652147e-07)
('afitient', 2.7900906113646474e-06)
('aflordable', 1.1967288061958614e-08)
('afnanthis', 0.0)
('afo', 2.1110547362475442e-06)
('afoard', 1.8851509489686925e-09)
('afong', 0.0)
('afoordable', 0.0)
('aforabla', 9.082127447550563e-09)
('aforable', 2.657927018999442e-07)
('aford', 2.5531968831348504e-06)
('afordabel', 3.2991040220927775e-07)
('afordabele', 0.0)
('afordable', 1.9933355613404955e-05)
('afordal', 0.0)
('afordale', 2.2433960235114953e-08)
('afordanle', 6.514266761607308e-07)
('afordavle', 1.4655725061142606e-07)
('aforde', 2.340225409220316e-08)
('afordqble', 2.52546085023658e-07)
('afordvel', 0.0)
('aforementioned', 3.839685148053732e-06)
('aforked', 1.0649689437154371e-07)
(

('aming', 0.0)
('amini', 2.2993345279398732e-07)
('aminimum', 2.0640143699771207e-06)
('amiold', 6.992809559198537e-08)
('amir', 3.8027301782775346e-06)
('amiracle', 1.1540463095753984e-08)
('amit', 1.778337149330367e-05)
('amitabh', 2.447595842433325e-06)
('amiya', 3.4993751630970523e-06)
('amize', 4.6998234719987666e-07)
('amizin', 1.2252407160434762e-08)
('amizing', 1.931442195004743e-06)
('amizinh', 4.0448791084943994e-08)
('amjad', 0.0)
('amke', 0.0)
('amkng', 1.6757852950512537e-08)
('amkozixbzizbzubzjisbsbns', 0.0)
('aml', 0.0)
('amla', 1.7643536712847616e-06)
('amle', 7.341790986267572e-06)
('amled', 1.7171148143788342e-08)
('amlesh', 1.8687132244615863e-06)
('amload', 3.6239617141649705e-09)
('amloade', 6.965345056709165e-08)
('amlod', 1.8382273528295928e-07)
('amlode', 3.7630522985398583e-07)
('amloded', 1.2879770921246142e-09)
('amlodled', 0.0)
('amloead', 6.184567782468373e-11)
('amloed', 1.2603860063683427e-06)
('amloeded', 6.427733732988498e-09)
('amloid', 8.6993351113491

('appericiate', 1.1579398752286754e-07)
('appericiateable', 6.176173612986155e-08)
('appericiating', 2.882847838138165e-08)
('apperience', 4.559879987564218e-10)
('appertain', 4.6212432155652994e-07)
('apperture', 1.1149638315940774e-07)
('appertute', 8.389429368153927e-10)
('appetite', 0.0)
('appeture', 4.135352819735531e-08)
('appfrom', 1.145170952428478e-09)
('appgood', 1.9078804823462325e-08)
('appgrade', 2.7169425445893796e-10)
('appgud', 7.273198433544924e-10)
('apphanging', 1.337787396304715e-06)
('appi', 6.109745015603408e-06)
('appication', 1.3184813350495693e-06)
('appie', 2.150571685288016e-07)
('appiee', 0.0)
('appience', 3.971725171780001e-06)
('appilaction', 1.5987241275985882e-06)
('appilcation', 1.3026650602696774e-06)
('appilication', 3.4055697633294003e-06)
('appin', 6.164391522052314e-08)
('apping', 1.04674833668651e-07)
('appit', 1.8890700783790262e-06)
('appits', 1.0013845449072535e-06)
('appke', 3.8301262549912674e-10)
('appkication', 0.0)
('appko', 0.0)
('appl', 

('auch', 1.7479879775189975e-09)
('aucha', 4.6142076141767794e-10)
('auche', 0.0)
('auchthere', 1.6082223922863903e-06)
('auctacore', 0.0)
('auction', 4.5778165332513955e-07)
('auctually', 2.0517910146494432e-06)
('auctully', 5.629720663004492e-08)
('aud', 1.794126730250511e-06)
('audable', 0.0)
('audeo', 6.380891602552497e-09)
('audi', 4.5821912441579225e-06)
('audia', 2.3699203970411774e-06)
('audiability', 0.0)
('audiable', 4.9847973668232e-07)
('audial', 1.8317409540745195e-09)
('audibality', 0.0)
('audibility', 2.3554181209385223e-06)
('audible', 4.4874166170688155e-05)
('audibledisplay', 1.4533025300305923e-06)
('audibleringtone', 3.5480580748210135e-06)
('audibly', 2.482879996450147e-11)
('audicity', 6.614487131558614e-08)
('audien', 0.0)
('audience', 1.5246310374198986e-05)
('audieo', 2.0011256775519185e-08)
('audince', 0.0)
('audio', 0.0002440958092528532)
('audioable', 3.913099946069577e-08)
('audiobass', 0.0)
('audiobel', 0.0)
('audioblethis', 3.303885905389693e-09)
('audioc

...

('unstalling', 1.1328491255365447e-10)
('unstatisfy', 1.6407225790359986e-10)
('unstopable', 5.714456587128952e-07)
('unstopble', 0.0)
('unstopeble', 1.0631629398233934e-08)
('unstoppable', 5.567727480274752e-06)
('unstopped', 3.1415389397862107e-09)
('unstuck', 1.428628211833808e-09)
('unstuckable', 0.0)
('unstylis', 4.029921963707823e-06)
('unsual', 2.2783382431340474e-06)
('unsually', 8.826074411773126e-09)
('unsub', 2.3092466927526474e-08)
('unsubscribe', 3.066102181378887e-08)
('unsucces', 1.5521899126295492e-06)
('unsuccesful', 1.4335095164400894e-08)
('unsuccessful', 4.625094687575905e-07)
('unsucessfull', 6.6136551103927115e-06)
('unsufficient', 4.901214247412804e-06)
('unsuitable', 2.6823229390270127e-06)
('unsuper', 6.113036937327807e-06)
('unsupporte', 2.485263563355522e-06)
('unsupported', 3.26735673405925e-06)
('unsure', 1.0865680197265652e-06)
('untaai', 0.0)
('untai', 5.1363876716491464e-11)
('untalkable', 0.0)
('untarnished', 0.0)
('unte', 5.301036904256017e-06)
('unter

('valuve', 1.531366474312812e-07)
('valuw', 1.7482979947431337e-06)
('valve', 1.1865233951328697e-06)
('valye', 2.2992616128987298e-07)
('valyrian', 0.0)
('valyu', 3.984939053472985e-06)
('vameback', 8.117557869802849e-08)
('vamer', 1.7625782330241108e-08)
('vamera', 3.460545228336837e-06)
('vamshi', 5.2369748842474395e-06)
('van', 5.71629135203521e-06)
('vanati', 0.0)
('vand', 1.684970922430369e-06)
('vanga', 1.1582448289660057e-07)
('vanguard', 1.5451965466246404e-08)
('vanila', 2.084588045053187e-08)
('vanilla', 1.270113554214168e-06)
('vanish', 1.3562864869690215e-05)
('vanquish', 4.707982350223168e-06)
('vansh', 0.0)
('vant', 2.6698862195139196e-06)
('vantage', 3.074978563156827e-07)
('vantilator', 4.428096642309072e-07)
('vaoice', 9.89156210896378e-07)
('vapas', 1.5955918048845662e-06)
('vapour', 0.0)
('var', 7.1299569925291595e-06)
('varaint', 1.6189856485763465e-06)
('varaku', 4.159984286026404e-09)
('varanasi', 3.6976876366719206e-06)
('varant', 0.0)
('varanty', 0.0)
('varast'

('vo', 8.665345187538117e-06)
('vobe', 5.75784775573515e-06)
('voble', 3.940806741608419e-06)
('vobleyibetter', 6.916496521043343e-08)
('vocal', 6.672988272582318e-06)
('voce', 5.895617919400595e-08)
('vocie', 1.3609792063665674e-08)
('vociferously', 0.0)
('voda', 5.511865369499142e-06)
('vodafone', 3.07087115774684e-05)
('vodaphone', 3.897205305896111e-06)
('vodeo', 0.0)
('vodi', 2.297872175630904e-10)
('vodio', 0.0)
('vodka', 6.382447266314487e-09)
('vody', 5.0211635614711855e-06)
('voewing', 0.0)
('vof', 7.656808342217322e-10)
('vofi', 4.7846448817092595e-11)
('vofinger', 0.0)
('vogue', 4.391426353114438e-06)
('voh', 3.2892118863327688e-09)
('voi', 2.0779795392139032e-07)
('voic', 7.557052266485615e-06)
('voice', 0.00046180500344319704)
('voiceand', 1.3589851366872182e-07)
('voiceeasy', 2.2561403900841795e-07)
('voicegood', 3.321243277767183e-10)
('voicein', 1.1725477914249084e-08)
('voiceit', 2.5062532269174764e-06)
('voicelg', 0.0)
('voicelock', 4.594918852654086e-07)
('voicemail'

('whille', 0.0)
('whilr', 9.369193356766554e-08)
('whilst', 6.120897511560497e-06)
('whimper', 0.0)
('whin', 8.54682258645783e-07)
('whine', 0.0)
('whing', 3.776610938249058e-07)
('whinge', 2.3933507758952324e-09)
('whinice', 1.6776251548479203e-09)
('whioch', 1.0715641639260174e-08)
('whiout', 1.153520147752043e-07)
('whip', 5.296571676718627e-07)
('whipe', 4.227464049263701e-08)
('whippet', 0.0)
('whis', 1.0585665182092523e-05)
('whisch', 6.033269574510116e-09)
('whise', 2.6150430813216156e-09)
('whish', 1.5509716557116185e-06)
('whisper', 1.0772177802208811e-08)
('whistle', 6.29659797023974e-06)
('whit', 2.060772614240426e-05)
('whita', 4.8584437107695644e-08)
('whitch', 1.2137662693282432e-05)
('white', 0.00017819861305991616)
('whitebattery', 4.498484898765493e-09)
('whiteboard', 1.9760081148959756e-06)
('whitebut', 9.610606174544582e-10)
('whitedisplay', 1.0642737237557163e-09)
('whitedisplayphysical', 0.0)
('whitefield', 1.9529640095031147e-06)
('whitei', 0.0)
('whitein', 1.7737

('xiaomicoolpad', 3.524635302962467e-11)
('xiaomidesign', 8.35575980827405e-08)
('xiaomie', 4.912664738772851e-07)
('xiaomieasy', 0.0)
('xiaomihave', 2.218504615291992e-09)
('xiaomii', 1.311730051815643e-07)
('xiaomiiam', 3.460578896814345e-08)
('xiaomiif', 3.077259182552378e-07)
('xiaomiiiii', 2.1926939288750385e-11)
('xiaomiiiiiiiiiii', 8.623027232140124e-11)
('xiaomiit', 1.9137060951003656e-09)
('xiaomikiller', 5.887632249341844e-09)
('xiaomilauche', 1.8648443625243806e-10)
('xiaomilook', 2.739271254445263e-06)
('xiaomilooksmetal', 0.0)
('xiaomime', 3.779562264156689e-09)
('xiaomimi', 2.486354277483688e-07)
('xiaomimimix', 3.5281479427258515e-06)
('xiaomimobiles', 1.3017459612398748e-06)
('xiaomimodel', 3.372033133065527e-06)
('xiaomin', 0.0)
('xiaomini', 3.307520927559043e-08)
('xiaominis', 7.562661566921915e-10)
('xiaominow', 0.0)
('xiaomipersnally', 0.0)
('xiaomipros', 3.776878831337618e-08)
('xiaomiradmi', 1.2573448551465812e-06)
('xiaomire', 0.0)
('xiaomiredmi', 2.4515776789191

In [47]:
List_Importance_indicators =[]
for feature_importance in clf_Gini.feature_importances_:
    List_Importance_indicators.append(feature_importance)

In [48]:
set(List_Importance_indicators)

{0.0,
 3.892698885011248e-06,
 1.0656481208684742e-07,
 2.536162241995704e-06,
 1.2540587022175919e-06,
 7.533702728506112e-08,
 3.9547330746147475e-08,
 4.065407779338548e-07,
 1.0087546800515545e-08,
 4.5221781907008625e-09,
 7.808194482139833e-07,
 1.5055649612355003e-05,
 8.461126412887107e-07,
 1.7614638681970985e-09,
 6.813877468494375e-09,
 1.2448709459103434e-10,
 1.1353392893207292e-07,
 1.4898963058916347e-06,
 3.24348558290028e-10,
 9.75489921129835e-10,
 2.4007125034698393e-06,
 8.433517007204794e-09,
 3.329540733057182e-08,
 2.7554801818168118e-06,
 7.276536848753014e-07,
 2.2700672843838546e-06,
 3.319657069374035e-11,
 2.5953380315985075e-05,
 5.7075453716230105e-08,
 1.1596077371642996e-11,
 1.2716157036809388e-08,
 6.404832242169208e-09,
 2.9382365480416263e-10,
 3.425570582773136e-06,
 1.5259388444171417e-08,
 7.896005651685348e-09,
 3.2671819099303197e-06,
 1.9218930449783334e-07,
 4.7293751645453335e-11,
 2.1254852527194627e-06,
 4.167361595553711e-09,
 8.3138428408

In [49]:
#We will use these importance scores to rank our features; in the following part, 
#we will select those features that have feature importance more than 0.001 for model training:
#Select features which have higher contribution in the final prediction
sfm_Gini = SelectFromModel(clf_Gini, threshold=0.0003) 

In [50]:
sfm_Gini


SelectFromModel(estimator=RandomForestClassifier(bootstrap=True, ccp_alpha=0.0,
                                                 class_weight=None,
                                                 criterion='gini',
                                                 max_depth=None,
                                                 max_features='auto',
                                                 max_leaf_nodes=None,
                                                 max_samples=None,
                                                 min_impurity_decrease=0.0,
                                                 min_impurity_split=None,
                                                 min_samples_leaf=1,
                                                 min_samples_split=2,
                                                 min_weight_fraction_leaf=0.0,
                                                 n_estimators=100, n_jobs=None,
                                                 oob_score=False,

In [51]:
#selecting features
Important_Features = []
for feature, importance in zip(feat_labels, clf_Gini.feature_importances_):
    if importance >=0.0003:
        Important_Features.append(feature)
        

In [52]:
len(Important_Features)

547

In [53]:
Important_Features

['able',
 'accord',
 'actually',
 'add',
 'advertisement',
 'affordable',
 'ago',
 'alot',
 'amazing',
 'amazon',
 'amoled',
 'android',
 'app',
 'apple',
 'application',
 'ask',
 'asus',
 'attractive',
 'auto',
 'automatically',
 'available',
 'average',
 'awesome',
 'awsome',
 'b',
 'backup',
 'bad',
 'base',
 'basic',
 'battery',
 'beast',
 'beautiful',
 'bed',
 'best',
 'better',
 'big',
 'bit',
 'black',
 'blast',
 'blur',
 'body',
 'brand',
 'break',
 'bring',
 'brother',
 'bt',
 'budget',
 'bug',
 'build',
 'button',
 'buy',
 'c',
 'cam',
 'camera',
 'capacity',
 'capture',
 'card',
 'care',
 'case',
 'cause',
 'cell',
 'center',
 'centre',
 'change',
 'charge',
 'charger',
 'charging',
 'cheap',
 'cheat',
 'check',
 'china',
 'chinese',
 'chipset',
 'choice',
 'choose',
 'clarity',
 'class',
 'clear',
 'click',
 'color',
 'colour',
 'come',
 'comfortable',
 'common',
 'company',
 'compare',
 'comparison',
 'con',
 'condition',
 'connect',
 'contact',
 'contain',
 'cool',
 'cool

In [54]:
#Select features which have higher contribution in the final prediction
sfm_Gini.fit(X_transformed, y)

SelectFromModel(estimator=RandomForestClassifier(bootstrap=True, ccp_alpha=0.0,
                                                 class_weight=None,
                                                 criterion='gini',
                                                 max_depth=None,
                                                 max_features='auto',
                                                 max_leaf_nodes=None,
                                                 max_samples=None,
                                                 min_impurity_decrease=0.0,
                                                 min_impurity_split=None,
                                                 min_samples_leaf=1,
                                                 min_samples_split=2,
                                                 min_weight_fraction_leaf=0.0,
                                                 n_estimators=100, n_jobs=None,
                                                 oob_score=False,

In [55]:
#Transform input dataset

X_transformed_1 = sfm_Gini.transform(X_transformed) 

In [56]:
#Xtest_1= sfm.transform(X_test)

In [57]:
X_transformed_1.shape

(160057, 547)

In [58]:
len(Important_Features)

547

In [59]:
len(y)

160057

In [60]:
#len(y_test)

In [61]:
X_Gini_Index=pd.DataFrame(X_transformed_1.todense(),columns = Important_Features )

In [62]:
X_Gini_Index.head(100)

able  accord  actually  add  advertisement  affordable  ago  alot  \
0    0.0     0.0       0.0  0.0            0.0         0.0  0.0   0.0   
1    0.0     0.0       0.0  0.0            0.0         0.0  0.0   0.0   
2    0.0     0.0       0.0  0.0            0.0         0.0  0.0   0.0   
3    0.0     0.0       0.0  0.0            0.0         0.0  0.0   0.0   
4    0.0     0.0       0.0  0.0            0.0         0.0  0.0   0.0   
..   ...     ...       ...  ...            ...         ...  ...   ...   
95   0.0     0.0       0.0  0.0            0.0         0.0  0.0   0.0   
96   0.0     0.0       0.0  0.0            0.0         0.0  0.0   0.0   
97   0.0     0.0       0.0  0.0            0.0         0.0  0.0   0.0   
98   0.0     0.0       0.0  0.0            0.0         0.0  0.0   0.0   
99   0.0     0.0       0.0  0.0            0.0         0.0  0.0   0.0   

    amazing  amazon  ...  wrost    x    xiaomi  xiomi  year  yes   yu  \
0       0.0     0.0  ...    0.0  0.0  0.097237    0.0   0.0  0.0  0.0   
1       0.0     0.0  ...    0.0  0.0  0.000000    0.0   0.0  0.0  0.0   
2       0.0     0.0  ...    0.0  0.0  0.261142    0.0   0.0  0.0  0.0   
3       0.0     0.0  ...    0.0  0.0  0.092806    0.0   0.0  0.0  0.0   
4       0.0     0.0  ...    0.0  0.0  0.000000    0.0   0.0  0.0  0.0   
..      ...     ...  ...    ...  ...       ...    ...   ...  ...  ...   
95      0.0     0.0  ...    0.0  0.0  0.000000    0.0   0.0  0.0  0.0   
96      0.0     0.0  ...    0.0  0.0  0.000000    0.0   0.0  0.0  0.0   
97      0.0     0.0  ...    0.0  0.0  0.000000    0.0   0.0  0.0  0.0   
98      0.0     0.0  ...    0.0  0.0  0.000000    0.0   0.0  0.0  0.0   
99      0.0     0.0  ...    0.0  0.0  0.000000    0.0   0.0  0.0  0.0   

    yuphoria  yureka  zenfone  
0        0.0     0.0      0.0  
1        0.0     0.0      0.0  
2        0.0     0.0      0.0  
3        0.0     0.0      0.0  
4        0.0     0.0      0.0  
..       ...     ...      ...  
95       0.0     0.0      0.0  
96       0.0     0.0      0.0  
97       0.0     0.0      0.0  
98       0.0     0.0      0.0  
99       0.0     0.0      0.0  

[100 rows x 547 columns]

In [63]:
X_Gini_Index.shape

(160057, 547)

In [64]:
X_Gini_Index.to_csv("X_Gini_Index.csv",header = True, index = False)

### Choosing Important features using Features Importance (Information Gain)

In [65]:
#Random Forests allow us to look at feature importances, which is the how much the Gini Index 
#for a feature decreases at each split. The more the Gini Index decreases for a feature, 
#the more important it is. The figure below rates the features from 0–100, with 100 being the most important.
#Import Random Forest classifier class from sklearn
from sklearn.ensemble import RandomForestClassifier
#from sklearn.tree import DecisionTreeClassifier


In [66]:
#Import feature selector
from sklearn.feature_selection import SelectFromModel


In [67]:
#Train, Test split
#X_train, X_test, y_train, y_test = train_test_split(X_transformed, y, test_size = 0.3, random_state = 1001)

In [68]:
#Extract attribute names from the data frame
#feat = data.keys()
#feat_labels = feat.get_values()


feat_labels=tfidf.get_feature_names()
feat_labels

['aa',
 'aaa',
 'aaaa',
 'aaaaaaa',
 'aaaaaaaaaaa',
 'aaaaaaaaaaaaaaaa',
 'aaaaaaaaaaaaaaaaaaaaaaaaaaaaa',
 'aaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaa',
 'aaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaa',
 'aaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaa',
 'aaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaa',
 'aaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaashdhdhdbdbdbdhdxbhdhxbhdhdhebdhdhdbdbdbdbbdbdhdhdbdbc',
 'aaaaaaaaaaaaaaaaaaawwwwwwwwwwwooooooooooooooooooossssssssssssssssssssssooooooooooooooooommmmmmmmmmmmmmmmmmmmmmeeeeeeeeeeeeeeee',
 'aaaaaaaaaaaaaaamazing',
 'aaaaaaaaaaaaaaawwwwwwweeeeeeeeeeeeeeeeeeesssssssssssssssssssssssssssssss',
 'aaaaaaaaaa

In [69]:
#Create a random forest classifier with the following Parameters
trees = 100
#max_feat= 8
#max_depth = 30

In [70]:
clf_IG = RandomForestClassifier(n_estimators=trees,

criterion='entropy',

#max_features=max_feat,

#max_depth=max_depth,

random_state=0,)


In [71]:
#Train the classifier 
clf_IG.fit(X_transformed, y)

RandomForestClassifier(bootstrap=True, ccp_alpha=0.0, class_weight=None,
                       criterion='entropy', max_depth=None, max_features='auto',
                       max_leaf_nodes=None, max_samples=None,
                       min_impurity_decrease=0.0, min_impurity_split=None,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, n_estimators=100,
                       n_jobs=None, oob_score=False, random_state=0, verbose=0,
                       warm_start=False)

In [72]:
pre_IG = clf_IG.predict(X_transformed)

In [73]:
len(pre_IG)


160057

In [74]:
#Function to evaluate model performance

def getAccuracy(pre,ytest): 
    count = 0
    for i in range(len(ytest)):
        if ytest[i]==pre[i]: 
            count+=1
            acc = float(count)/len(ytest)
            return acc

In [75]:
#Evaluate the model performance for the test data
target_names = ['class 0', 'class 1']
ClassificationReport_IG=classification_report(y, pre_IG, target_names=target_names)
ClassificationReport_IG

#'              precision    recall  f1-score   support\n\n     
#class 0       1.00      1.00      1.00     25866\n     
#class 1       1.00      1.00      1.00    134191\n\n    
#accuracy                          1.00    160057\n   
#macro avg     1.00      1.00      1.00    160057\n
#weighted avg  1.00      1.00      1.00    160057\n'

'              precision    recall  f1-score   support\n\n     class 0       1.00      1.00      1.00     25866\n     class 1       1.00      1.00      1.00    134191\n\n    accuracy                           1.00    160057\n   macro avg       1.00      1.00      1.00    160057\nweighted avg       1.00      1.00      1.00    160057\n'

In [76]:
accuracy_score(y, pre_IG) #0.9999937522257696

0.9999875044515392

In [77]:
for feature in zip(feat_labels, clf_IG.feature_importances_):
    print(feature)

('aa', 3.361612565826867e-05)
('aaa', 5.159000849245046e-06)
('aaaa', 4.252682199389883e-06)
('aaaaaaa', 7.272493416146101e-08)
('aaaaaaaaaaa', 1.7609869968436222e-08)
('aaaaaaaaaaaaaaaa', 1.6589214959299024e-09)
('aaaaaaaaaaaaaaaaaaaaaaaaaaaaa', 2.6844286929745354e-08)
('aaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaa', 2.2079059266408133e-09)
('aaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaa', 1.0614525502691042e-08)
('aaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaa', 6.916473762191951e-08)
('aaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaa', 2.0785418109745222e-07)
('aaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaaashdhdhdbdbdbdhdxbhdhxbhdhdhebdhdhdbdbdbdbbd

('akshaynow', 8.89384790254234e-08)
('akshit', 1.2081350047679032e-07)
('akskdvfn', 0.0)
('akso', 5.334006370740783e-06)
('aksonos', 0.0)
('aktu', 3.116527717761536e-08)
('akward', 1.6541537009718445e-06)
('akwared', 1.8768596585250577e-06)
('akways', 1.5117665921881427e-07)
('al', 0.00016885760242920156)
('ala', 3.317843060008725e-08)
('alabaster', 1.6088448838982488e-06)
('alag', 4.377494257004862e-07)
('alaikomtoday', 1.3389093539931196e-08)
('alaikum', 7.1071101877233525e-06)
('alaikumi', 4.710516052018674e-07)
('alam', 7.994433373579283e-08)
('alambagh', 8.209111934398067e-08)
('alao', 7.5667954561076e-06)
('alaong', 4.656059984244351e-07)
('alaram', 1.4035785066817795e-09)
('alarege', 5.424129578321101e-08)
('alarge', 1.9970149174400945e-07)
('alarm', 1.5885385588982128e-05)
('alarmingly', 1.5082123298269699e-06)
('alart', 0.0)
('alas', 7.046046017418221e-06)
('alaso', 2.182642342561026e-06)
('alava', 9.306844871116277e-07)
('alavaa', 1.720939841863364e-09)
('alaviable', 1.069430

('androidbattery', 4.6751408233427475e-06)
('androidbest', 9.64305340662397e-08)
('androidbetter', 1.005833014507145e-06)
('androidbig', 0.0)
('androidbut', 1.4220344620521977e-06)
('androidcamera', 0.0)
('androidcemra', 0.0)
('androiddecent', 7.866325764053313e-09)
('androiddesign', 2.222753656634244e-07)
('androiddisplay', 9.024455919971085e-09)
('androiddual', 0.0)
('androiddust', 1.220445142514381e-07)
('androide', 8.027578074772685e-06)
('androidear', 4.860672566288502e-07)
('androidecosystem', 6.995797399803425e-06)
('androidgo', 0.0)
('androidgood', 1.0258273762439863e-06)
('androidgreat', 5.4118292359666345e-08)
('androidheight', 4.680086417154819e-09)
('androidhigher', 0.0)
('androidi', 7.18468988908505e-07)
('androidian', 7.561511077909015e-08)
('androidimprov', 1.4645719136830178e-09)
('androidimproved', 1.5222419797441858e-07)
('androidin', 1.6915272127174344e-08)
('androidit', 2.545842235941162e-07)
('androidlarge', 0.0)
('androidlatest', 0.0)
('androidlollipop', 1.1492709

('aso', 1.335639053146426e-07)
('asoeme', 4.6118010542243487e-08)
('asold', 2.7590672967370677e-06)
('asolid', 0.0)
('asom', 2.7764273617211315e-06)
('asome', 1.2975298843411631e-06)
('asomeicon', 7.401911768777456e-08)
('asoom', 0.0)
('asound', 6.163496405569973e-08)
('asowam', 4.9284634903200274e-08)
('asowem', 7.890188220693942e-08)
('asowm', 3.013343635439145e-07)
('asowme', 1.1580936606597754e-06)
('asowne', 5.087603727707462e-08)
('asowom', 5.372970644345052e-08)
('asowome', 9.696788569295869e-08)
('asowsome', 0.0)
('asp', 3.2627996128108077e-06)
('aspact', 1.7976282429668948e-07)
('aspal', 1.0633359140471742e-08)
('aspalt', 2.909951980843143e-06)
('aspalte', 6.610358848330229e-08)
('aspas', 5.48373237142651e-09)
('aspath', 7.1255614241888195e-09)
('aspe', 5.710854361782457e-06)
('aspec', 1.2013569921094483e-07)
('aspecial', 9.483463318690358e-08)
('aspecially', 4.46490504989672e-07)
('aspecification', 1.5360544746104367e-07)
('aspect', 0.00018054540282255523)
('aspectable', 3.04

('badlysung', 2.835077206857109e-06)
('badmain', 2.871758060584879e-06)
('badmobile', 3.3110221670267686e-06)
('badmore', 2.3661750126132467e-06)
('badmy', 9.23314449468473e-06)
('badness', 8.165102223791798e-06)
('badnetworks', 3.246785318469162e-06)
('badno', 3.6114128683550253e-06)
('badnot', 1.3315646807500445e-05)
('badnothe', 1.5448215253655551e-06)
('badon', 2.7703958693454483e-06)
('badone', 5.232572453782339e-06)
('badonly', 2.6714510502803796e-06)
('badother', 2.9844564501796254e-06)
('badoverall', 0.0)
('badphone', 4.0318987032250985e-06)
('badphoto', 0.0)
('badpoor', 1.1771693090766337e-06)
('badporfomance', 0.0)
('badprice', 2.207122391828518e-08)
('badprocessor', 3.056578989977919e-09)
('badprosavarage', 2.2805178842765617e-07)
('badram', 3.918817543063493e-06)
('badrear', 2.9333201462963916e-06)
('badrenge', 2.223407936152521e-06)
('badrukhan', 4.1144427510322106e-08)
('bads', 4.783811748248898e-06)
('badsamsung', 2.1287598768004766e-06)
('badscreen', 2.772454695096572e-

...

('uniqie', 0.0)
('uniqly', 6.087990981746438e-08)
('uniqness', 0.0)
('uniqu', 1.2607527806305964e-06)
('unique', 0.0004419553038078721)
('uniqueand', 0.0)
('uniquefeatures', 2.301483818353223e-08)
('uniquehigh', 0.0)
('uniqueit', 1.0074618447886986e-08)
('uniquelatest', 0.0)
('uniquely', 2.9017371652312147e-06)
('uniquene', 1.1815272312725946e-08)
('uniqueness', 1.371743484726598e-05)
('uniquenessat', 7.66067310770942e-08)
('uniquenessprice', 1.808952289591921e-08)
('uniquenokia', 4.1004674995379553e-07)
('uniqueprice', 1.3378984048143175e-07)
('uniquerange', 3.961530759214624e-06)
('uniqueredmi', 0.0)
('uniquethe', 0.0)
('uniquethi', 1.690915586510198e-06)
('uniqui', 2.8560364276379544e-08)
('uniquie', 2.8308560753497645e-09)
('uniquly', 4.9480063094309655e-08)
('unisex', 0.0)
('unistal', 2.033378268517578e-06)
('unistall', 2.314041762922809e-06)
('unistalle', 7.357622282831705e-09)
('unistallit', 3.3513561464582653e-06)
('unit', 8.964086058759365e-05)
('unite', 0.00021436305455538863

('usko', 8.855700175330623e-08)
('uslast', 1.1594738731308769e-07)
('usleased', 0.0)
('usleess', 5.978759551901952e-06)
('usless', 1.83796991126679e-05)
('usly', 2.3515780898336608e-08)
('usman', 4.2015119336261253e-07)
('usme', 1.2778601089972538e-06)
('usmese', 5.260888000896698e-07)
('usmw', 1.4430894745111676e-08)
('usne', 8.3005446158367e-09)
('usng', 7.800905087749384e-07)
('usnig', 1.1920540983740005e-07)
('usning', 9.771310610865448e-06)
('usnr', 2.875602065696026e-07)
('usoahuaiajaj', 1.043423611777127e-06)
('usoecially', 6.68431627374078e-08)
('usomg', 1.0122163047309204e-07)
('usong', 6.71409222317519e-07)
('usosos', 0.0)
('usp', 2.302172817681794e-05)
('uspar', 4.341922883579137e-07)
('uspit', 4.5543177309466074e-08)
('usr', 2.1100898104007525e-06)
('usram', 3.111030158680829e-06)
('usre', 3.0379274794248057e-06)
('usrear', 1.0311818796649973e-07)
('usregarde', 1.1668085379566291e-08)
('usrfull', 0.0)
('usrr', 1.2479161509698085e-08)
('uss', 1.1593340414298588e-06)
('ussage

('wage', 0.0)
('wager', 2.00098400192406e-08)
('waght', 0.0)
('wagth', 0.0)
('wagyra', 0.0)
('wah', 9.606158543314568e-08)
('waha', 1.0756238236243423e-08)
('wahat', 0.0)
('wahdat', 1.9854698043852152e-07)
('wahen', 2.5286694881356306e-08)
('wahhh', 1.954182067585086e-07)
('wahhhhh', 1.112698424035498e-08)
('wahi', 4.397818836836128e-08)
('wahin', 0.0)
('wahstapp', 0.0)
('waht', 3.3218681927489064e-06)
('wahts', 0.0)
('wahtsapp', 3.975259937397557e-07)
('wahtsp', 7.612471487041233e-07)
('wai', 3.8710201705717804e-08)
('waieghte', 0.0)
('waighat', 4.854861478524671e-08)
('waight', 1.0944611225937879e-05)
('waighte', 9.899830075814137e-07)
('waighted', 0.0)
('waightedamd', 8.499743012043327e-09)
('waightedgood', 6.167607249686331e-07)
('waigt', 5.709124242490726e-08)
('wail', 2.8281199631785746e-06)
('waild', 3.423468230533971e-08)
('wairy', 4.775398202739337e-08)
('wais', 1.0444668329645936e-06)
('waisa', 6.923586878934296e-09)
('waise', 7.792565392227705e-07)
('waist', 4.41414090674610

('worldcup', 0.0)
('worldest', 3.5644975833833007e-07)
('worldeverythe', 6.159020249372747e-08)
('worldfeature', 0.0)
('worldfuture', 0.0)
('worldgaming', 2.781629425432667e-06)
('worldhd', 2.3511429168787066e-07)
('worldhuge', 5.646508764375955e-08)
('worldhz', 0.0)
('worldi', 2.299300967190682e-07)
('worldif', 3.594524232004035e-07)
('worldin', 3.98462738376855e-08)
('worldit', 4.84541216965563e-07)
('worldits', 4.359419481978074e-06)
('worldj', 0.0)
('worldlarg', 0.0)
('worldlast', 4.14061577953574e-08)
('worldly', 0.0)
('worldnothing', 1.1338844050959137e-07)
('worldpartner', 4.3277807225018223e-07)
('worldpeople', 0.0)
('worldrecently', 4.159521367894655e-08)
('worldredmi', 2.4431302218210245e-08)
('worlds', 0.0)
('worldsamsun', 6.73087721743327e-08)
('worldsamsung', 5.467676482097508e-08)
('worldsdd', 1.2725499247156771e-08)
('worldso', 0.0)
('worldsound', 6.812299871513209e-08)
('worldstroage', 1.6844603092852002e-08)
('worldthat', 0.0)
('worldthats', 3.7946731733776232e-06)
('w

('zo', 6.082056691264268e-08)
('zoe', 2.4353841242140703e-08)
('zoloit', 0.0)
('zom', 4.822872126334444e-08)
('zombie', 0.0)
('zome', 0.0)
('zoming', 4.059684712987555e-08)
('zomming', 3.13720994824573e-07)
('zone', 2.6249870017096004e-05)
('zonefone', 1.7692651705805238e-08)
('zoner', 0.0)
('zong', 0.0)
('zoo', 4.10553302696398e-06)
('zook', 8.154761052685562e-08)
('zoom', 0.00021668017188351346)
('zoomable', 4.7724790894454826e-08)
('zoomdiiferent', 9.900092258268782e-09)
('zoomdisplay', 0.0)
('zoomed', 5.078230552998366e-07)
('zoomgood', 0.0)
('zoomi', 1.0031133459807245e-07)
('zoomig', 0.0)
('zoomin', 5.479404687168119e-09)
('zooming', 8.211770379684509e-06)
('zoomingand', 3.2584827826442006e-06)
('zoomit', 5.1068066204466467e-08)
('zoomnig', 0.0)
('zoomos', 1.8328689243628586e-07)
('zoomthere', 0.0)
('zoop', 7.3343878377224345e-09)
('zopo', 0.0)
('zoppo', 2.2235591254242886e-06)
('zora', 1.947239528438064e-08)
('zordaar', 2.5304185192406193e-08)
('zphone', 3.087661828586284e-06)
(

In [78]:
List_Importance_indicators =[]
for feature_importance in clf_IG.feature_importances_:
    List_Importance_indicators.append(feature_importance)

In [79]:
set(List_Importance_indicators)

{0.0,
 3.2016487259534448e-09,
 7.64257822539087e-06,
 7.415167147490604e-08,
 4.4124567352819266e-05,
 1.9348135547898318e-08,
 2.405541863590445e-07,
 2.6305997496475424e-09,
 4.0844042826708264e-08,
 1.724106369901505e-08,
 2.095019772242669e-05,
 4.127306112879185e-05,
 3.270725983538141e-07,
 4.0442455430781084e-07,
 7.121343534167545e-09,
 1.7556044442585986e-07,
 3.399119702864986e-05,
 0.00011001977577509528,
 3.617096809032718e-07,
 1.76523485636716e-07,
 1.6115097881505964e-07,
 1.947239528438064e-08,
 2.4516225529066935e-08,
 6.500117706656655e-07,
 1.245650196360358e-06,
 6.99037631700286e-09,
 4.3890224791810133e-07,
 2.0836524055043976e-09,
 3.530770982698524e-07,
 1.0293908758330463e-05,
 2.3580411153023284e-06,
 4.4728608377302043e-07,
 2.688081303863549e-05,
 4.6004765868242074e-07,
 4.102958022659613e-09,
 2.3822394772590447e-08,
 1.308431296825352e-05,
 3.485170964318671e-06,
 5.632706461787302e-07,
 4.62398588805713e-07,
 2.9317562265424857e-09,
 4.5378101839609635e

In [80]:
#We will use these importance scores to rank our features; in the following part, 
#we will select those features that have feature importance more than 0.0003 for model training:
#Select features which have higher contribution in the final prediction
sfm_IG = SelectFromModel(clf_IG, threshold=0.0003) 

In [81]:
#selecting features
Important_Features_IG = []
for feature, importance in zip(feat_labels, clf_IG.feature_importances_):
    if importance >=0.0003:
        Important_Features_IG.append(feature)
        
len(Important_Features_IG)       

565

In [82]:
sfm_IG


SelectFromModel(estimator=RandomForestClassifier(bootstrap=True, ccp_alpha=0.0,
                                                 class_weight=None,
                                                 criterion='entropy',
                                                 max_depth=None,
                                                 max_features='auto',
                                                 max_leaf_nodes=None,
                                                 max_samples=None,
                                                 min_impurity_decrease=0.0,
                                                 min_impurity_split=None,
                                                 min_samples_leaf=1,
                                                 min_samples_split=2,
                                                 min_weight_fraction_leaf=0.0,
                                                 n_estimators=100, n_jobs=None,
                                                 oob_score=Fal

In [83]:
#selecting features
Important_Features_IG = []
for feature, importance in zip(feat_labels, clf_IG.feature_importances_):
    if importance >= 0.0003:
        Important_Features_IG.append(feature)
        

In [84]:
len(Important_Features_IG)

565

In [85]:
Important_Features_IG

['able',
 'accord',
 'actually',
 'add',
 'affordable',
 'ago',
 'alot',
 'amazing',
 'amazon',
 'amoled',
 'android',
 'app',
 'apple',
 'application',
 'ask',
 'asus',
 'attractive',
 'auto',
 'automatically',
 'available',
 'average',
 'awesome',
 'awsome',
 'b',
 'backup',
 'bad',
 'base',
 'basic',
 'batter',
 'battery',
 'battry',
 'beast',
 'beautiful',
 'bed',
 'best',
 'better',
 'big',
 'bit',
 'black',
 'blast',
 'blur',
 'body',
 'brand',
 'break',
 'brilliant',
 'bring',
 'brother',
 'bt',
 'budget',
 'bug',
 'build',
 'button',
 'buy',
 'c',
 'cam',
 'camara',
 'camera',
 'capacity',
 'capture',
 'card',
 'care',
 'case',
 'cell',
 'center',
 'centre',
 'change',
 'charge',
 'charger',
 'charging',
 'cheap',
 'cheat',
 'check',
 'china',
 'chinese',
 'chipset',
 'choice',
 'choose',
 'clarity',
 'class',
 'clear',
 'click',
 'color',
 'colour',
 'come',
 'comfortable',
 'common',
 'company',
 'compare',
 'con',
 'condition',
 'connect',
 'contain',
 'cool',
 'coolpad',
 '

In [86]:
#Select features which have higher contribution in the final prediction
sfm_IG.fit(X_transformed, y)

SelectFromModel(estimator=RandomForestClassifier(bootstrap=True, ccp_alpha=0.0,
                                                 class_weight=None,
                                                 criterion='entropy',
                                                 max_depth=None,
                                                 max_features='auto',
                                                 max_leaf_nodes=None,
                                                 max_samples=None,
                                                 min_impurity_decrease=0.0,
                                                 min_impurity_split=None,
                                                 min_samples_leaf=1,
                                                 min_samples_split=2,
                                                 min_weight_fraction_leaf=0.0,
                                                 n_estimators=100, n_jobs=None,
                                                 oob_score=Fal

In [87]:
X_transformed.shape

(160057, 101644)

In [88]:
#Transform input dataset

X_transformed_1 = sfm_IG.transform(X_transformed) 

In [89]:
#Xtest_1= sfm.transform(X_test)

In [90]:
X_transformed_1.shape

(160057, 565)

In [91]:
len(Important_Features_IG)

565

In [92]:
len(y)

160057

In [93]:
#len(y_test)

In [94]:
X_IG_Index=pd.DataFrame(X_transformed_1.todense(),columns = Important_Features_IG )

In [95]:
X_IG_Index.head()

able  accord  actually  add  affordable  ago  alot  amazing  amazon  \
0   0.0     0.0       0.0  0.0         0.0  0.0   0.0      0.0     0.0   
1   0.0     0.0       0.0  0.0         0.0  0.0   0.0      0.0     0.0   
2   0.0     0.0       0.0  0.0         0.0  0.0   0.0      0.0     0.0   
3   0.0     0.0       0.0  0.0         0.0  0.0   0.0      0.0     0.0   
4   0.0     0.0       0.0  0.0         0.0  0.0   0.0      0.0     0.0   

   amoled  ...  wrost    x    xiaomi  xiomi  year  yes   yu  yuphoria  yureka  \
0     0.0  ...    0.0  0.0  0.097237    0.0   0.0  0.0  0.0       0.0     0.0   
1     0.0  ...    0.0  0.0  0.000000    0.0   0.0  0.0  0.0       0.0     0.0   
2     0.0  ...    0.0  0.0  0.261142    0.0   0.0  0.0  0.0       0.0     0.0   
3     0.0  ...    0.0  0.0  0.092806    0.0   0.0  0.0  0.0       0.0     0.0   
4     0.0  ...    0.0  0.0  0.000000    0.0   0.0  0.0  0.0       0.0     0.0   

   zenfone  
0      0.0  
1      0.0  
2      0.0  
3      0.0  
4      0.0  

[5 rows x 565 columns]

In [96]:
X_IG_Index.to_csv("X_IG_Index.csv",header = True, index = False)

In [97]:
#Three wordvectors generated using Chi Square, Gini Index and Information Gain

In [98]:
features_df.head()

able  advertise  advertisement  affordable  ago  alot  amazing  android  \
0   0.0        0.0            0.0         0.0  0.0   0.0      0.0      0.0   
1   0.0        0.0            0.0         0.0  0.0   0.0      0.0      0.0   
2   0.0        0.0            0.0         0.0  0.0   0.0      0.0      0.0   
3   0.0        0.0            0.0         0.0  0.0   0.0      0.0      0.0   
4   0.0        0.0            0.0         0.0  0.0   0.0      0.0      0.0   

   angry  app  ...  world  worst  worth  worthless  wrong  wrost    x  \
0    0.0  0.0  ...    0.0    0.0    0.0        0.0    0.0    0.0  0.0   
1    0.0  0.0  ...    0.0    0.0    0.0        0.0    0.0    0.0  0.0   
2    0.0  0.0  ...    0.0    0.0    0.0        0.0    0.0    0.0  0.0   
3    0.0  0.0  ...    0.0    0.0    0.0        0.0    0.0    0.0  0.0   
4    0.0  0.0  ...    0.0    0.0    0.0        0.0    0.0    0.0  0.0   

     xiaomi   yu  yureka  
0  0.097237  0.0     0.0  
1  0.000000  0.0     0.0  
2  0.261142  0.0     0.0  
3  0.092806  0.0     0.0  
4  0.000000  0.0     0.0  

[5 rows x 300 columns]

In [99]:
features_df.shape

(160057, 300)

In [100]:
X_Gini_Index.head()

able  accord  actually  add  advertisement  affordable  ago  alot  amazing  \
0   0.0     0.0       0.0  0.0            0.0         0.0  0.0   0.0      0.0   
1   0.0     0.0       0.0  0.0            0.0         0.0  0.0   0.0      0.0   
2   0.0     0.0       0.0  0.0            0.0         0.0  0.0   0.0      0.0   
3   0.0     0.0       0.0  0.0            0.0         0.0  0.0   0.0      0.0   
4   0.0     0.0       0.0  0.0            0.0         0.0  0.0   0.0      0.0   

   amazon  ...  wrost    x    xiaomi  xiomi  year  yes   yu  yuphoria  yureka  \
0     0.0  ...    0.0  0.0  0.097237    0.0   0.0  0.0  0.0       0.0     0.0   
1     0.0  ...    0.0  0.0  0.000000    0.0   0.0  0.0  0.0       0.0     0.0   
2     0.0  ...    0.0  0.0  0.261142    0.0   0.0  0.0  0.0       0.0     0.0   
3     0.0  ...    0.0  0.0  0.092806    0.0   0.0  0.0  0.0       0.0     0.0   
4     0.0  ...    0.0  0.0  0.000000    0.0   0.0  0.0  0.0       0.0     0.0   

   zenfone  
0      0.0  
1      0.0  
2      0.0  
3      0.0  
4      0.0  

[5 rows x 547 columns]

In [101]:
X_Gini_Index.shape

(160057, 547)

In [102]:
X_IG_Index.head()

able  accord  actually  add  affordable  ago  alot  amazing  amazon  \
0   0.0     0.0       0.0  0.0         0.0  0.0   0.0      0.0     0.0   
1   0.0     0.0       0.0  0.0         0.0  0.0   0.0      0.0     0.0   
2   0.0     0.0       0.0  0.0         0.0  0.0   0.0      0.0     0.0   
3   0.0     0.0       0.0  0.0         0.0  0.0   0.0      0.0     0.0   
4   0.0     0.0       0.0  0.0         0.0  0.0   0.0      0.0     0.0   

   amoled  ...  wrost    x    xiaomi  xiomi  year  yes   yu  yuphoria  yureka  \
0     0.0  ...    0.0  0.0  0.097237    0.0   0.0  0.0  0.0       0.0     0.0   
1     0.0  ...    0.0  0.0  0.000000    0.0   0.0  0.0  0.0       0.0     0.0   
2     0.0  ...    0.0  0.0  0.261142    0.0   0.0  0.0  0.0       0.0     0.0   
3     0.0  ...    0.0  0.0  0.092806    0.0   0.0  0.0  0.0       0.0     0.0   
4     0.0  ...    0.0  0.0  0.000000    0.0   0.0  0.0  0.0       0.0     0.0   

   zenfone  
0      0.0  
1      0.0  
2      0.0  
3      0.0  
4      0.0  

[5 rows x 565 columns]

In [103]:
X_IG_Index.shape

(160057, 565)

In [104]:
#combining Features selected using Chi-Square, Gini Index and Information Gain using Union method

In [105]:
X_Train_CF=pd.DataFrame(pd.concat([features_df,X_Gini_Index],axis=1,join = 'inner'))

In [106]:
X_Train_CF.shape

(160057, 847)

In [107]:
X_Train_CF.head()

able  advertise  advertisement  affordable  ago  alot  amazing  android  \
0   0.0        0.0            0.0         0.0  0.0   0.0      0.0      0.0   
1   0.0        0.0            0.0         0.0  0.0   0.0      0.0      0.0   
2   0.0        0.0            0.0         0.0  0.0   0.0      0.0      0.0   
3   0.0        0.0            0.0         0.0  0.0   0.0      0.0      0.0   
4   0.0        0.0            0.0         0.0  0.0   0.0      0.0      0.0   

   angry  app  ...  wrost    x    xiaomi  xiomi  year  yes   yu  yuphoria  \
0    0.0  0.0  ...    0.0  0.0  0.097237    0.0   0.0  0.0  0.0       0.0   
1    0.0  0.0  ...    0.0  0.0  0.000000    0.0   0.0  0.0  0.0       0.0   
2    0.0  0.0  ...    0.0  0.0  0.261142    0.0   0.0  0.0  0.0       0.0   
3    0.0  0.0  ...    0.0  0.0  0.092806    0.0   0.0  0.0  0.0       0.0   
4    0.0  0.0  ...    0.0  0.0  0.000000    0.0   0.0  0.0  0.0       0.0   

   yureka  zenfone  
0     0.0      0.0  
1     0.0      0.0  
2     0.0      0.0  
3     0.0      0.0  
4     0.0      0.0  

[5 rows x 847 columns]

In [108]:
len(set(X_Train_CF.columns))#unique features

625

In [109]:
X_Train_CF=pd.DataFrame(pd.concat([X_Train_CF,X_IG_Index],axis=1,join = 'inner'))

In [110]:
X_Train_CF.shape

(160057, 1412)

In [111]:
X_Train_CF.head()

able  advertise  advertisement  affordable  ago  alot  amazing  android  \
0   0.0        0.0            0.0         0.0  0.0   0.0      0.0      0.0   
1   0.0        0.0            0.0         0.0  0.0   0.0      0.0      0.0   
2   0.0        0.0            0.0         0.0  0.0   0.0      0.0      0.0   
3   0.0        0.0            0.0         0.0  0.0   0.0      0.0      0.0   
4   0.0        0.0            0.0         0.0  0.0   0.0      0.0      0.0   

   angry  app  ...  wrost    x    xiaomi  xiomi  year  yes   yu  yuphoria  \
0    0.0  0.0  ...    0.0  0.0  0.097237    0.0   0.0  0.0  0.0       0.0   
1    0.0  0.0  ...    0.0  0.0  0.000000    0.0   0.0  0.0  0.0       0.0   
2    0.0  0.0  ...    0.0  0.0  0.261142    0.0   0.0  0.0  0.0       0.0   
3    0.0  0.0  ...    0.0  0.0  0.092806    0.0   0.0  0.0  0.0       0.0   
4    0.0  0.0  ...    0.0  0.0  0.000000    0.0   0.0  0.0  0.0       0.0   

   yureka  zenfone  
0     0.0      0.0  
1     0.0      0.0  
2     0.0      0.0  
3     0.0      0.0  
4     0.0      0.0  

[5 rows x 1412 columns]

In [112]:
len(set(X_Train_CF.columns))#unique features

661

In [114]:
#def getDuplicateColumns(df):

#    duplicateColumnNames = set()
#    # Iterate over all the columns in dataframe
#    for x in range(df.shape[1]):
#        # Select column at xth index.
#        col = df.iloc[:, x]
#        # Iterate over all the columns in DataFrame from (x+1)th index till end
#        for y in range(x + 1, df.shape[1]):
#            # Select column at yth index.
#            otherCol = df.iloc[:, y]
#            # Check if two columns at x 7 y index are equal
#            if col.equals(otherCol):
#                duplicateColumnNames.add(df.columns.values[y])
 
#    return list(duplicateColumnNames)

In [115]:
#print('*** Find duplicate Columns in a DataFrame ***')
 
## Get list of duplicate columns
#duplicateColumnNames = getDuplicateColumns(X_Train_CF)
 
#print('Duplicate Columns are as follows')
#for col in duplicateColumnNames:
#    print('Column name : ', col)
 
#    print('*** Remove duplicate Columns in a DataFrame ***')
 
#    # Delete duplicate columns
#    X_Train_CF_commonfeatures = X_Train_CF.drop(columns=getDuplicateColumns(X_Train_CF))
 
#    print("Modified Dataframe", X_Train_CF_commonfeatures, sep='\n')

In [116]:

X_Train_CF = pd.DataFrame(X_Train_CF.loc[:,~X_Train_CF.columns.duplicated()])

In [117]:
X_Train_CF.shape

(160057, 661)

In [118]:
X_Train_CF.columns

Index(['able', 'advertise', 'advertisement', 'affordable', 'ago', 'alot',
       'amazing', 'android', 'angry', 'app',
       ...
       'result', 'rs', 'simply', 'strong', 'technology', 'thank', 'trust',
       'turbo', 'wait', 'water'],
      dtype='object', length=661)

In [119]:
X_Train_CF.shape


(160057, 661)

In [120]:
X_Train_CF['Product'] = LatestMobileReviews1['Product']
X_Train_CF.head()

able  advertise  advertisement  affordable  ago  alot  amazing  android  \
0   0.0        0.0            0.0         0.0  0.0   0.0      0.0      0.0   
1   0.0        0.0            0.0         0.0  0.0   0.0      0.0      0.0   
2   0.0        0.0            0.0         0.0  0.0   0.0      0.0      0.0   
3   0.0        0.0            0.0         0.0  0.0   0.0      0.0      0.0   
4   0.0        0.0            0.0         0.0  0.0   0.0      0.0      0.0   

   angry  app  ...   rs  simply  strong  technology  thank  trust  turbo  \
0    0.0  0.0  ...  0.0     0.0     0.0         0.0    0.0    0.0    0.0   
1    0.0  0.0  ...  0.0     0.0     0.0         0.0    0.0    0.0    0.0   
2    0.0  0.0  ...  0.0     0.0     0.0         0.0    0.0    0.0    0.0   
3    0.0  0.0  ...  0.0     0.0     0.0         0.0    0.0    0.0    0.0   
4    0.0  0.0  ...  0.0     0.0     0.0         0.0    0.0    0.0    0.0   

   wait  water              Product  
0   0.0    0.0  Xiaomi Redmi Note 3  
1   0.0    0.0  Xiaomi Redmi Note 3  
2   0.0    0.0  Xiaomi Redmi Note 3  
3   0.0    0.0  Xiaomi Redmi Note 3  
4   0.0    0.0  Xiaomi Redmi Note 3  

[5 rows x 662 columns]

In [121]:
X = X_Train_CF
y= LatestMobileReviews1 ['positive_negative']

In [122]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.3, random_state = 1001)

In [123]:
X_train.columns

Index(['able', 'advertise', 'advertisement', 'affordable', 'ago', 'alot',
       'amazing', 'android', 'angry', 'app',
       ...
       'rs', 'simply', 'strong', 'technology', 'thank', 'trust', 'turbo',
       'wait', 'water', 'Product'],
      dtype='object', length=662)

In [124]:
X_train.shape, y_train.shape, X_test.shape, y_test.shape

((112039, 662), (112039,), (48018, 662), (48018,))

In [125]:
#excluding Product variable from both the train and test dataset
#X_train = pd.DataFrame(X_train.loc[:,-X_train['Product']])
#X_test = pd.DataFrame(X_test.loc[:,-X_test['Product']])
X_train1=X_train.iloc[:,0:661]
X_train1.columns
X_test1=X_test.iloc[:,0:661]
X_test1.columns

Index(['able', 'advertise', 'advertisement', 'affordable', 'ago', 'alot',
       'amazing', 'android', 'angry', 'app',
       ...
       'result', 'rs', 'simply', 'strong', 'technology', 'thank', 'trust',
       'turbo', 'wait', 'water'],
      dtype='object', length=661)

### Selecting Final Featuers using statistical methods based on features selected by Gini Index, Chi Square and Information Gain

### Features Selection using combined approach of Chi Square, Gini Index and Information Gain  and LinearSVC (Support Vector Classifier)

In [126]:
from sklearn.svm import LinearSVC#change

#from sklearn.model_selection import GridSearchCV 

In [127]:
#Final Data with Final Featues Selection using ChiSquare, Gini Index and Information Gain

In [128]:
#create base classifier
clf_CF_SVM = LinearSVC()

In [129]:
#fitting model
clf_CF_SVM.fit(X_train1, y_train)


LinearSVC(C=1.0, class_weight=None, dual=True, fit_intercept=True,
          intercept_scaling=1, loss='squared_hinge', max_iter=1000,
          multi_class='ovr', penalty='l2', random_state=None, tol=0.0001,
          verbose=0)

In [130]:
#Evaluating model on test data
y_pred_CF_SVM = clf_CF_SVM.predict(X_test1)

In [131]:
target_names = ['class 0', 'class 1']
ClassificationReport_CF_SVM=classification_report(y_test, y_pred_CF_SVM, target_names=target_names)
ClassificationReport_CF_SVM

#'              precision    recall  f1-score   support\n\n     
#class 0       0.81      0.51      0.63      7791\n     
#class 1       0.91      0.98      0.94     40227\n\n    
#accuracy                          0.90     48018\n   
#macro avg     0.86      0.74      0.78     48018\n
#weighted avg  0.90      0.90      0.89     48018\n'

'              precision    recall  f1-score   support\n\n     class 0       0.81      0.51      0.63      7791\n     class 1       0.91      0.98      0.94     40227\n\n    accuracy                           0.90     48018\n   macro avg       0.86      0.74      0.78     48018\nweighted avg       0.90      0.90      0.89     48018\n'

In [132]:
ConfusionMatrix_CF_SVM=confusion_matrix(y_test, y_pred_CF_SVM)
ConfusionMatrix_CF_SVM

array([[ 3975,  3816],
       [  929, 39298]], dtype=int64)

In [133]:
accuracy_score(y_test, y_pred_CF_SVM) #0.9011620642259153 accuracy of base model

0.9011828897496772

In [134]:
y_pred_CF_SVM = pd.DataFrame(y_pred_CF_SVM,X_test['Product'])
y_pred_CF_SVM.rename(columns={0:"Tags_CF_SVM"}, inplace = True)
y_pred_CF_SVM.head(5)
#len(y_pred_CF_SVM)
y_pred_CF_SVM.to_csv("y_pred_CF_SVM.csv",header = True)

### Features Selection using combined approach of Chi Square, Gini Index and Information Gain and Logistic Regression Classifier


In [135]:
from sklearn import linear_model

#create base classifier
clf_CF_LR= linear_model.LogisticRegression()


#fitting model
clf_CF_LR.fit(X_train1, y_train)



C:\Users\halapets\AppData\Local\Continuum\anaconda3\lib\site-packages\sklearn\linear_model\_logistic.py:939: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html.
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  extra_warning_msg=_LOGISTIC_SOLVER_CONVERGENCE_MSG)


LogisticRegression(C=1.0, class_weight=None, dual=False, fit_intercept=True,
                   intercept_scaling=1, l1_ratio=None, max_iter=100,
                   multi_class='auto', n_jobs=None, penalty='l2',
                   random_state=None, solver='lbfgs', tol=0.0001, verbose=0,
                   warm_start=False)

In [136]:
#Evaluating model on test data
y_pred_CF_LR = clf_CF_LR.predict(X_test1)

In [137]:
target_names = ['class 0', 'class 1']
ClassificationReport_CF_LR=classification_report(y_test, y_pred_CF_LR, target_names=target_names)
ClassificationReport_CF_LR

#'              precision    recall  f1-score   support\n\n     
#class 0       0.81      0.51      0.62      7791\n     
#class 1       0.91      0.98      0.94     40227\n\n    
#accuracy                          0.90     48018\n   
#macro avg     0.86      0.74      0.78     48018\n
#weighted avg  0.89      0.90      0.89     48018\n'

'              precision    recall  f1-score   support\n\n     class 0       0.81      0.51      0.62      7791\n     class 1       0.91      0.98      0.94     40227\n\n    accuracy                           0.90     48018\n   macro avg       0.86      0.74      0.78     48018\nweighted avg       0.89      0.90      0.89     48018\n'

In [138]:
ClassificationReport_CF_LR=confusion_matrix(y_test, y_pred_CF_LR)
ClassificationReport_CF_LR

array([[ 3968,  3823],
       [  941, 39286]], dtype=int64)

In [139]:
accuracy_score(y_test, y_pred_CF_LR) #0.9007872047982006 accuracy of base model

0.9007872047982006

In [140]:
y_pred_CF_LR = pd.DataFrame(y_pred_CF_LR,X_test['Product'])
y_pred_CF_LR.rename(columns={0:"Tags_CF_LR"}, inplace = True)
y_pred_CF_LR.head(5)
#len(y_pred_CF_LR)
y_pred_CF_LR.to_csv("y_pred_CF_LR.csv",header = True)

### Features Selection using combined approach of Chi Square, Gini Index and Information Gain and Naive Bayes Classifier


In [141]:
from sklearn.naive_bayes import BernoulliNB

#create base classifier
clf_CF_NB = BernoulliNB()

#fitting model
clf_CF_NB.fit(X_train1, y_train)

BernoulliNB(alpha=1.0, binarize=0.0, class_prior=None, fit_prior=True)

In [142]:
#Evaluating model on test data
y_pred_CF_NB = clf_CF_NB.predict(X_test1)

In [143]:
target_names = ['class 0', 'class 1']
ClassificationReport_CF_NB=classification_report(y_test, y_pred_CF_NB, target_names=target_names)
ClassificationReport_CF_NB

#'              precision    recall  f1-score   support\n\n     
#class 0       0.59      0.66      0.62      7791\n     
#class 1       0.93      0.91      0.92     40227\n\n    
#accuracy                          0.87     48018\n   
#macro avg     0.76      0.79      0.77     48018\n
#weighted avg  0.88      0.87      0.87     48018\n'

'              precision    recall  f1-score   support\n\n     class 0       0.59      0.66      0.62      7791\n     class 1       0.93      0.91      0.92     40227\n\n    accuracy                           0.87     48018\n   macro avg       0.76      0.79      0.77     48018\nweighted avg       0.88      0.87      0.87     48018\n'

In [144]:
ConfusionMatrix_CF_NB=confusion_matrix(y_test, y_pred_CF_NB)
ConfusionMatrix_CF_NB

array([[ 5145,  2646],
       [ 3552, 36675]], dtype=int64)

In [146]:
accuracy_score(y_test, y_pred_CF_NB) #0.8709234037236037 accuracy of base model

0.8709234037236037

In [147]:
y_pred_CF_NB = pd.DataFrame(y_pred_CF_NB,X_test['Product'])
y_pred_CF_NB.rename(columns={0:"Tags_CF_NB"}, inplace = True)
y_pred_CF_NB.head(5)
#len(y_pred_CF_NB)
y_pred_CF_NB.to_csv("y_pred_CF_NB.csv",header = True)

### Features Selection using combined approach of Chi Square, Gini Index and Information Gain and Decision Tree Classifier

In [148]:
from sklearn.tree import DecisionTreeClassifier 

#create base classifier
clf_CF_CART = DecisionTreeClassifier(criterion = "gini", 
            random_state = 100)

#fitting model
clf_CF_CART.fit(X_train1, y_train)

DecisionTreeClassifier(ccp_alpha=0.0, class_weight=None, criterion='gini',
                       max_depth=None, max_features=None, max_leaf_nodes=None,
                       min_impurity_decrease=0.0, min_impurity_split=None,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, presort='deprecated',
                       random_state=100, splitter='best')

In [149]:
#Evaluating model on test data
y_pred_CF_CART = clf_CF_CART.predict(X_test1)

In [150]:
target_names = ['class 0', 'class 1']
ClassificationReport_CF_CART=classification_report(y_test, y_pred_CF_CART, target_names=target_names)
ClassificationReport_CF_CART

#'              precision    recall  f1-score   support\n\n     
#class 0       0.50      0.49      0.50      7791\n     
#class 1       0.90      0.91      0.90     40227\n\n    
#accuracy                          0.84     48018\n   
#macro avg     0.70      0.70      0.70     48018\n
#weighted avg  0.84      0.84      0.84     48018\n'

'              precision    recall  f1-score   support\n\n     class 0       0.50      0.49      0.50      7791\n     class 1       0.90      0.91      0.90     40227\n\n    accuracy                           0.84     48018\n   macro avg       0.70      0.70      0.70     48018\nweighted avg       0.84      0.84      0.84     48018\n'

In [151]:
ConfusionMatrix_CF_CART=confusion_matrix(y_test, y_pred_CF_CART)
ConfusionMatrix_CF_CART

array([[ 3845,  3946],
       [ 3773, 36454]], dtype=int64)

In [152]:
accuracy_score(y_test, y_pred_CF_CART) #0.8392477820817194 accuracy of base model

0.8392477820817194

In [153]:
y_pred_CF_CART = pd.DataFrame(y_pred_CF_CART,X_test['Product'])
y_pred_CF_CART.rename(columns={0:"Tags_CF_CART"}, inplace = True)
y_pred_CF_CART.head(5)
#len(y_pred_CF_CART)
y_pred_CF_CART.to_csv("y_pred_CF_CART.csv",header = True)

In [154]:
#Ensemble Model based on Individual Classifiers using Majority of voting

In [155]:
y_pred_CF_NB = pd.read_csv("y_pred_CF_NB.csv",index_col=None)
y_pred_CF_LR= pd.read_csv("y_pred_CF_LR.csv",index_col=None)
y_pred_CF_CART= pd.read_csv("y_pred_CF_CART.csv",index_col=None)
y_pred_CF_SVM= pd.read_csv("y_pred_CF_SVM.csv",index_col=None)

In [156]:
y_pred_CF_ensb=y_pred_CF_NB.merge(y_pred_CF_LR, how = 'inner',left_index = True, right_index = True, on = 'Product')


In [157]:
y_pred_CF_ensb = y_pred_CF_ensb.merge(y_pred_CF_CART, how='inner', left_index = True, right_index = True, on = 'Product')

In [158]:
y_pred_CF_ensb.shape

(48018, 4)

In [159]:

y_pred_CF_ensb.head()

Product  Tags_CF_NB  Tags_CF_LR  Tags_CF_CART
0        Xiaomi Redmi 4A           1           1             1
1         Lenovo K3 Note           1           1             0
2  Samsung Galaxy Note 3           1           1             1
3    Xiaomi Redmi Note 3           1           1             1
4  Xiaomi Redmi 3S Prime           1           1             1

In [160]:
y_pred_CF_ensb = y_pred_CF_ensb.merge(y_pred_CF_SVM, how='inner', left_index = True, right_index = True, on = 'Product')

In [161]:

y_pred_CF_ensb.columns

Index(['Product', 'Tags_CF_NB', 'Tags_CF_LR', 'Tags_CF_CART', 'Tags_CF_SVM'], dtype='object')

In [162]:
#Adding weights on classifiers based on the performance of the classifiers in terms of accuracy, precision and recall
#Naive Bayes and Decision Tree has been added a weight of 0.5 each
y_pred_CF_ensb["Total Votes"] = (0.5*y_pred_CF_ensb["Tags_CF_NB"])+y_pred_CF_ensb["Tags_CF_LR"] + (0.5*y_pred_CF_ensb["Tags_CF_CART"])+y_pred_CF_ensb["Tags_CF_SVM"]


In [163]:
y_pred_CF_ensb["Majority of Votes"]  = [1 if x >=2 else 0 for x in y_pred_CF_ensb["Total Votes"]] 

In [164]:
target_names = ['class 0', 'class 1']
ClassificationReport_CF_Ensemble=classification_report(y_test, y_pred_CF_ensb["Majority of Votes"], target_names=target_names)
ClassificationReport_CF_Ensemble

#'              precision    recall  f1-score   support\n\n     
#class 0       0.80      0.53      0.64      7791\n     
#class 1       0.91      0.97      0.94     40227\n\n    
#accuracy                          0.90     48018\n   
#macro avg     0.86      0.75      0.79     48018\n
#weighted avg  0.90      0.90      0.89     48018\n'



'              precision    recall  f1-score   support\n\n     class 0       0.80      0.53      0.64      7791\n     class 1       0.91      0.97      0.94     40227\n\n    accuracy                           0.90     48018\n   macro avg       0.86      0.75      0.79     48018\nweighted avg       0.90      0.90      0.89     48018\n'

In [165]:
ConfusionMatrix_CF_Ensemble=confusion_matrix(y_test, y_pred_CF_ensb["Majority of Votes"])
ConfusionMatrix_CF_Ensemble

array([[ 4122,  3669],
       [ 1022, 39205]], dtype=int64)

In [166]:
accuracy_score(y_test, y_pred_CF_ensb["Majority of Votes"]) #0.9029114082219167 accuracy of base model

0.902307468032821

In [168]:
### Ensemble Model on Count Vectorization-Feature Importance (Classifiers used- Decision Tree, Naive Bayes, Decision Tree and Logistic Regression)

from sklearn import model_selection
from sklearn.linear_model import LogisticRegression
from sklearn.tree import DecisionTreeClassifier
from sklearn.svm import SVC
from sklearn.naive_bayes import BernoulliNB
from sklearn.ensemble import VotingClassifier

seed = 7
kfold = model_selection.KFold(n_splits=3, random_state=seed)
# create the sub models
estimators = []
model1 = LogisticRegression()
estimators.append(('logistic', model1))
model2 = DecisionTreeClassifier()
estimators.append(('cart', model2))
model3 = SVC()
estimators.append(('svm', model3))
model4 = BernoulliNB()
estimators.append(('NB', model4))
# create the ensemble model
ensemble = VotingClassifier(estimators)


results_FI = model_selection.cross_val_score(ensemble, X.iloc[:,0:661], y, cv=kfold)




C:\Users\halapets\AppData\Local\Continuum\anaconda3\lib\site-packages\sklearn\model_selection\_split.py:296: FutureWarning: Setting a random_state has no effect since shuffle is False. This will raise an error in 0.24. You should leave random_state to its default (None), or set shuffle=True.
  FutureWarning
C:\Users\halapets\AppData\Local\Continuum\anaconda3\lib\site-packages\sklearn\linear_model\_logistic.py:939: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html.
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  extra_warning_msg=_LOGISTIC_SOLVER_CONVERGENCE_MSG)
C:\Users\halapets\AppData\Local\Continuum\anaconda3\lib\site-packages\sklearn\linear_model\_logistic.py:939: ConvergenceWarning: lbf

In [169]:

print(results_FI.mean()) #mean estimate of classification accuracy 0.898617300337587



0.898617300337587


In [170]:

results_FI.std()# Standard Deviation for classification accuracy 0.008621765263168941

0.008621765263168941